In [6]:
# Original: alphatools/fundamentals/make_fundamentals.py
# Modified: ajjc
# Date: 2019-01-15
# Download SF1 data from Quandl account, add zipline quandl bundle Equity.sid column, and save to 'sharadar_with_sid.pkl'
#    which is ready for ingestion into Fundamentals class.
from zipline.data import bundles
from zipline.pipeline import Pipeline
from zipline.pipeline.data import USEquityPricing
from zipline.pipeline.data import Column  
from zipline.pipeline.data import DataSet
from zipline.pipeline.engine import SimplePipelineEngine
from zipline.pipeline.filters import StaticAssets
from zipline.pipeline.loaders import USEquityPricingLoader
from zipline.pipeline.loaders.frame import DataFrameLoader
from zipline.utils.calendars import get_calendar

import numpy as np
import pandas as pd

trading_calendar = get_calendar('NYSE')
###Old-orig bundle_data = bundles.load('quandl')
bundle_data = bundles.load('sharadar-prices')

In [7]:
#bundle_data

In [8]:
#data_file = '/home/ubuntu/hca/quandl_data/SHARADAR_SF1_086134faf658fcc2cdcb53f4295b5fad.zip
#data_file = '/home/ubuntu/hca/quandl_data/SHARADAR_SF1_086134faf658fcc2cdcb53f4295b5fad_20190603.zip'

QUANDL_DATA_DIR    ='/home/ubuntu/hca/quandl_data/'
### FUNDAMENTALS_DAILY ='SHARADAR_SF1_0902195e140925ca23756cd43d9f89ae-2020-02-27.zip'
FUNDAMENTALS_DAILY ='SHARADAR_SF1_0902195e140925ca23756cd43d9f89ae.csv'
data_file = QUANDL_DATA_DIR + FUNDAMENTALS_DAILY
df = pd.read_csv(data_file)#, nrows=1000)

In [9]:
#print(df.head())
#print(df.describe())

In [10]:
df=df[(df.dimension=='ARQ')] # Only take As-Reported-Quarterly (ARQ) dimension

In [11]:
df.loc[:,'Date'] = pd.to_datetime(df.calendardate)

In [12]:
#df['sid'] = 0 #original: np.nan
df.set_index('Date', inplace=True)
df.info()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 96908 entries, 2015-03-31 to 2019-12-31
Columns: 111 entries, ticker to workingcapital
dtypes: float64(105), object(6)
memory usage: 82.8+ MB


In [13]:
if df.index.tzinfo is None:
    df.index = df.index.tz_localize('UTC')
dates = df.index.unique()
print("NumberOfDates={} Dates={}".format(len(dates),dates))

NumberOfDates=21 Dates=DatetimeIndex(['2015-03-31', '2015-06-30', '2015-09-30', '2015-12-31',
               '2016-03-31', '2016-06-30', '2016-09-30', '2016-12-31',
               '2017-03-31', '2017-06-30', '2017-09-30', '2017-12-31',
               '2018-03-31', '2018-06-30', '2018-09-30', '2018-12-31',
               '2019-03-31', '2019-06-30', '2019-09-30', '2019-12-31',
               '2020-03-31'],
              dtype='datetime64[ns, UTC]', name='Date', freq=None)


In [14]:
#df.index

In [15]:
### df= df[['calendardate','ticker','de']]

In [16]:
#df.loc[dates[0]]
#df.index.to_series().apply(str)
#df.index.to_series()[0]
#df.apply(lambda row:pd.to_datetime(row.calendardate), axis=1)
### df.apply(lambda row:bundle_data.asset_finder.lookup_symbol(row.ticker,as_of_date=pd.to_datetime(row.calendardate).tz_localize('US/Eastern')), axis=1)
def get_sid(row):
    ticker = row.ticker
    day = pd.to_datetime(row.calendardate).tz_localize('US/Eastern')
    
    this_ticker = None
    try:
        this_ticker = bundle_data.asset_finder.lookup_symbol(ticker, as_of_date= day)
        this_sid = this_ticker.sid
        print("Good:Date={} ticker = {} result={} this_sid={}".format(day, ticker, this_ticker, this_sid))

    except:
        #this_sid = np.nan
        this_sid = -1
        print("Bad:Date={} ticker = {} result={} this_sid={}".format(day, ticker, this_ticker, this_sid))
    return this_sid

In [17]:
# Main computation of linking Sharadar SF1 Fundamentals Tabe to 
df['sid'] = df.apply(get_sid, axis=1)

Good:Date=2015-03-31 00:00:00-04:00 ticker = A result=Equity(0 [A]) this_sid=0
Good:Date=2015-06-30 00:00:00-04:00 ticker = A result=Equity(0 [A]) this_sid=0
Good:Date=2015-09-30 00:00:00-04:00 ticker = A result=Equity(0 [A]) this_sid=0
Good:Date=2015-12-31 00:00:00-05:00 ticker = A result=Equity(0 [A]) this_sid=0
Good:Date=2016-03-31 00:00:00-04:00 ticker = A result=Equity(0 [A]) this_sid=0
Good:Date=2016-06-30 00:00:00-04:00 ticker = A result=Equity(0 [A]) this_sid=0
Good:Date=2016-09-30 00:00:00-04:00 ticker = A result=Equity(0 [A]) this_sid=0
Good:Date=2016-12-31 00:00:00-05:00 ticker = A result=Equity(0 [A]) this_sid=0
Good:Date=2017-03-31 00:00:00-04:00 ticker = A result=Equity(0 [A]) this_sid=0
Good:Date=2017-06-30 00:00:00-04:00 ticker = A result=Equity(0 [A]) this_sid=0
Good:Date=2017-09-30 00:00:00-04:00 ticker = A result=Equity(0 [A]) this_sid=0
Good:Date=2017-12-31 00:00:00-05:00 ticker = A result=Equity(0 [A]) this_sid=0
Good:Date=2018-03-31 00:00:00-04:00 ticker = A resul

In [18]:
#df.head()

In [19]:
#import pixiedust

In [20]:
#file_tickers = df.loc[dates[0]][['ticker', 'sid']]
#print(file_tickers)
#len(file_tickers)

In [21]:
##### WARNING: ajjc: Does not work, yet idea used for working usage of get_sid function.
###%%pixie_debugger
##sids = pd.Series(0,index=df.index)
#df['sid'] = -1 # Add column of all -1 to dataframe df
#for day in dates:
#    file_tickers = df.loc[day]['ticker']
#    #sids = []
#    for ticker in file_tickers:
#        this_ticker= None
#        this_sid = None
#        try:
#            this_ticker = bundle_data.asset_finder.lookup_symbol(ticker, as_of_date=day)
#            this_sid = this_ticker.sid
#            print("Good:Date={} ticker = {} result={} this_sid={}".format(day, ticker, this_ticker, this_sid))
#
#        except:
#            #this_sid = np.nan
#            this_sid = -1
#            print("Bad:Date={} ticker = {} result={} this_sid={}".format(day, ticker, this_ticker, this_sid))
# 
#        df[day]=this_sid
#
##df['sid'] = pd.Series(sids, index=df.index)  #Set sid column all at once, at end. The sid column is the ZipLine bundle integer mapping Equity.sid
#df['sid'] = sids  #Set sid column all at once, at end. The sid column is the ZipLine bundle integer mapping Equity.sid

In [22]:
#df.sid

In [23]:
#df[df.ticker.str.contains('AAPL')]
#a_sym=bundle_data.asset_finder.lookup_symbol('A',as_of_date=pd.to_datetime('2014-03-31').tz_localize('UTC') )
#aapl_sym=bundle_data.asset_finder.lookup_symbol('AAPL',as_of_date=pd.to_datetime('2014-03-31').tz_localize('UTC') )
#print(a_sym, aapl_sym)

In [24]:
#type(a_sym.sid)

In [25]:
#import pixiedust
#bundle_data.asset_finder.lookup_symbol('AAPL',as_of_date=pd.to_datetime('2014-03-31').tz_localize('UTC') )

In [32]:
# Don't need this as df is mostly float64 already
#df['pb'] =  pd.to_numeric(df['pb'], errors='coerce')

df.to_pickle(QUANDL_DATA_DIR + 'sharadar_sf1_with_sid-2020-05-01.pkl')


In [27]:
#Final sanity check
print(df.info())
#[type(df[x][0]) for x in df.columns] #dtypes: float64(105), int64(1), object(6)    NOTE: All objects are strings. the sid column is int64, with 0 encoding NA
print([x for x in df.columns])
df.head()

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 96908 entries, 2015-03-31 to 2019-12-31
Columns: 112 entries, ticker to sid
dtypes: float64(105), int64(1), object(6)
memory usage: 83.5+ MB
None
['ticker', 'dimension', 'calendardate', 'datekey', 'reportperiod', 'lastupdated', 'accoci', 'assets', 'assetsavg', 'assetsc', 'assetsnc', 'assetturnover', 'bvps', 'capex', 'cashneq', 'cashnequsd', 'cor', 'consolinc', 'currentratio', 'de', 'debt', 'debtc', 'debtnc', 'debtusd', 'deferredrev', 'depamor', 'deposits', 'divyield', 'dps', 'ebit', 'ebitda', 'ebitdamargin', 'ebitdausd', 'ebitusd', 'ebt', 'eps', 'epsdil', 'epsusd', 'equity', 'equityavg', 'equityusd', 'ev', 'evebit', 'evebitda', 'fcf', 'fcfps', 'fxusd', 'gp', 'grossmargin', 'intangibles', 'intexp', 'invcap', 'invcapavg', 'inventory', 'investments', 'investmentsc', 'investmentsnc', 'liabilities', 'liabilitiesc', 'liabilitiesnc', 'marketcap', 'ncf', 'ncfbus', 'ncfcommon', 'ncfdebt', 'ncfdiv', 'ncff', 'ncfi', 'ncfinv', 'ncfo', 'ncfx', 'n

ticker dimension calendardate     datekey  \
Date                                                                  
2015-03-31 00:00:00+00:00      A       ARQ   2015-03-31  2015-06-05   
2015-06-30 00:00:00+00:00      A       ARQ   2015-06-30  2015-09-02   
2015-09-30 00:00:00+00:00      A       ARQ   2015-09-30  2015-12-21   
2015-12-31 00:00:00+00:00      A       ARQ   2015-12-31  2016-03-08   
2016-03-31 00:00:00+00:00      A       ARQ   2016-03-31  2016-06-07   

                          reportperiod lastupdated       accoci        assets  \
Date                                                                            
2015-03-31 00:00:00+00:00   2015-04-30  2020-03-03 -270000000.0  7.412000e+09   
2015-06-30 00:00:00+00:00   2015-07-31  2020-03-03 -332000000.0  7.251000e+09   
2015-09-30 00:00:00+00:00   2015-10-31  2020-03-03 -391000000.0  7.479000e+09   
2015-12-31 00:00:00+00:00   2016-01-31  2020-03-03 -438000000.0  7.302000e+09   
2016-03-31 00:00:00+00:00   2016-04-30  2020-03-03 -299000000.0  7.640000e+09   

                           assetsavg       assetsc ...      shareswa  \
Date                                               ...                 
2015-03-31 00:00:00+00:00        NaN  3.620000e+09 ...   334000000.0   
2015-06-30 00:00:00+00:00        NaN  3.478000e+09 ...   332000000.0   
2015-09-30 00:00:00+00:00        NaN  3.686000e+09 ...   330000000.0   
2015-12-31 00:00:00+00:00        NaN  3.399000e+09 ...   329000000.0   
2016-03-31 00:00:00+00:00        NaN  3.488000e+09 ...   326000000.0   

                           shareswadil    sps     tangibles  taxassets  \
Date                                                                     
2015-03-31 00:00:00+00:00  337000000.0  2.883  4.555000e+09        0.0   
2015-06-30 00:00:00+00:00  334000000.0  3.054  4.401000e+09        0.0   
2015-09-30 00:00:00+00:00  332000000.0  3.136  4.668000e+09        0.0   
2015-12-31 00:00:00+00:00  332000000.0  3.125  4.311000e+09        0.0   
2016-03-31 00:00:00+00:00  328000000.0  3.126  4.594000e+09        0.0   

                               taxexp  taxliabilities   tbvps  workingcapital  \
Date                                                                            
2015-03-31 00:00:00+00:00   8000000.0             0.0  13.638    2.690000e+09   
2015-06-30 00:00:00+00:00  23000000.0             0.0  13.256    2.625000e+09   
2015-09-30 00:00:00+00:00         0.0             0.0  14.145    2.710000e+09   
2015-12-31 00:00:00+00:00  19000000.0             0.0  13.103    2.452000e+09   
2016-03-31 00:00:00+00:00  26000000.0             0.0  14.092    2.355000e+09   

                           sid  
Date                            
2015-03-31 00:00:00+00:00    0  
2015-06-30 00:00:00+00:00    0  
2015-09-30 00:00:00+00:00    0  
2015-12-31 00:00:00+00:00    0  
2016-03-31 00:00:00+00:00    0  

[5 rows x 112 columns]

In [28]:
I=df[df.ticker=='AAPL']

In [29]:
I.head()

ticker dimension calendardate     datekey  \
Date                                                                  
2015-03-31 00:00:00+00:00   AAPL       ARQ   2015-03-31  2015-04-28   
2015-06-30 00:00:00+00:00   AAPL       ARQ   2015-06-30  2015-07-22   
2015-09-30 00:00:00+00:00   AAPL       ARQ   2015-09-30  2015-10-28   
2015-12-31 00:00:00+00:00   AAPL       ARQ   2015-12-31  2016-01-27   
2016-03-31 00:00:00+00:00   AAPL       ARQ   2016-03-31  2016-04-27   

                          reportperiod lastupdated        accoci  \
Date                                                               
2015-03-31 00:00:00+00:00   2015-03-28  2020-01-29  2.710000e+09   
2015-06-30 00:00:00+00:00   2015-06-27  2020-01-29  1.098000e+09   
2015-09-30 00:00:00+00:00   2015-09-26  2020-01-29 -3.450000e+08   
2015-12-31 00:00:00+00:00   2015-12-26  2020-01-29 -1.480000e+09   
2016-03-31 00:00:00+00:00   2016-03-26  2020-01-29 -1.048000e+09   

                                 assets  assetsavg       assetsc ...   \
Date                                                             ...    
2015-03-31 00:00:00+00:00  2.611940e+11        NaN  6.789100e+10 ...    
2015-06-30 00:00:00+00:00  2.731510e+11        NaN  7.095300e+10 ...    
2015-09-30 00:00:00+00:00  2.904790e+11        NaN  8.937800e+10 ...    
2015-12-31 00:00:00+00:00  2.932840e+11        NaN  7.621900e+10 ...    
2016-03-31 00:00:00+00:00  3.052770e+11        NaN  8.759200e+10 ...    

                               shareswa   shareswadil     sps     tangibles  \
Date                                                                          
2015-03-31 00:00:00+00:00  5.793799e+09  5.834858e+09  10.012  2.524220e+11   
2015-06-30 00:00:00+00:00  5.729886e+09  5.773099e+09   8.657  2.643280e+11   
2015-09-30 00:00:00+00:00  5.646918e+09  5.682516e+09   9.120  2.814700e+11   
2015-12-31 00:00:00+00:00  5.558930e+09  5.594127e+09  13.649  2.841580e+11   
2016-03-31 00:00:00+00:00  5.514381e+09  5.540886e+09   9.168  2.961850e+11   

                              taxassets        taxexp  taxliabilities   tbvps  \
Date                                                                            
2015-03-31 00:00:00+00:00  5.141000e+09  4.995000e+09             0.0  43.568   
2015-06-30 00:00:00+00:00  5.010000e+09  3.796000e+09             0.0  46.131   
2015-09-30 00:00:00+00:00  5.546000e+09  3.938000e+09             0.0  49.845   
2015-12-31 00:00:00+00:00  0.000000e+00  6.212000e+09             0.0  51.117   
2016-03-31 00:00:00+00:00  0.000000e+00  3.626000e+09             0.0  53.711   

                           workingcapital  sid  
Date                                            
2015-03-31 00:00:00+00:00    9.162000e+09   21  
2015-06-30 00:00:00+00:00    5.668000e+09   21  
2015-09-30 00:00:00+00:00    8.768000e+09   21  
2015-12-31 00:00:00+00:00    1.270000e+08   21  
2016-03-31 00:00:00+00:00    1.932700e+10   21  

[5 rows x 112 columns]

In [30]:
!pwd

/home/ubuntu/hca/alphatools/notebooks
